## Import dependencies

In [1]:
!pip install transformers[sentencepiece]
!pip install datasets
!pip install fugashi ipadic
!pip install unidic_lite
!apt-get install git-lfs

     |████████████████████████████████| 4.0 MB 12.0 MB/s 
     |████████████████████████████████| 77 kB 4.7 MB/s 
     |████████████████████████████████| 6.5 MB 12.2 MB/s 
     |████████████████████████████████| 895 kB 23.2 MB/s 
     |████████████████████████████████| 596 kB 37.7 MB/s 
     |████████████████████████████████| 1.2 MB 44.6 MB/s 
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13
     |████████████████████████████████| 325 kB 12.2 MB/s 
     |████████████████████████████████| 1.1 MB 46.2 MB/s 
     |████████████████████████████████| 212 kB 55.0 MB/s 
     |████████████████████████████████| 136 kB 53.4 MB/s 
     |████████████████████████████████| 127 kB 5.9 MB/s 
     |████████████████████████████████| 271 kB 52.5 MB/s 
     |████████████████████████████████| 144 kB 55.3 MB/s 
     |████████████████████████████████| 94 kB 3.5 MB/s 
  Attempting uninstall: urllib3
    Found ex

## Load the data from the Hub

In [41]:
from datasets import load_dataset
jaquad_data = load_dataset('SkelterLabsInc/JaQuAD')

Using custom data configuration default
Reusing dataset ja_qu_ad (/root/.cache/huggingface/datasets/SkelterLabsInc___ja_qu_ad/default/0.1.0/5847b2e2ab5e02de284395bb15f87f13eae8f6f6ff1f01e4ee9c5c0dcf8ef8eb)


  0%|          | 0/2 [00:00<?, ?it/s]

In [17]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer

model = AutoModelForQuestionAnswering.from_pretrained("rinna/japanese-roberta-base")
tokenizer = AutoTokenizer.from_pretrained("rinna/japanese-roberta-base", use_fast=True)
tokenizer.do_lower_case = True 

Some weights of the model checkpoint at rinna/japanese-roberta-base were not used when initializing RobertaForQuestionAnswering: ['lm_head.decoder.weight', 'lm_head.layer_norm.weight', 'lm_head.dense.bias', 'lm_head.layer_norm.bias', 'lm_head.decoder.bias', 'lm_head.bias', 'lm_head.dense.weight']
- This IS expected if you are initializing RobertaForQuestionAnswering from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForQuestionAnswering from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForQuestionAnswering were not initialized from the model checkpoint at rinna/japanese-roberta-base and are newly initialized: ['qa_outputs.bias', 'qa_outputs.weight']
You should probably TRA

In [18]:
def preprocess_function(examples):
    questions = [q.strip() for q in examples["question"]]
    inputs = tokenizer(
        questions,
        examples["context"],
        max_length=384,
        truncation="only_second",
        return_offsets_mapping=True,
        padding="max_length",
    )

    offset_mapping = inputs.pop("offset_mapping")
    answers = examples["answers"]
    start_positions = []
    end_positions = []

    for i, offset in enumerate(offset_mapping):
        answer = answers[i]
        start_char = answer["answer_start"][0]
        end_char = answer["answer_start"][0] + len(answer["text"][0])
        sequence_ids = inputs.sequence_ids(i)

        # Find the start and end of the context
        idx = 0
        while sequence_ids[idx] != 1:
            idx += 1
        context_start = idx
        while sequence_ids[idx] == 1:
            idx += 1
        context_end = idx - 1

        # If the answer is not fully inside the context, label it (0, 0)
        if offset[context_start][0] > end_char or offset[context_end][1] < start_char:
            start_positions.append(0)
            end_positions.append(0)
        else:
            # Otherwise it's the start and end token positions
            idx = context_start
            while idx <= context_end and offset[idx][0] <= start_char:
                idx += 1
            start_positions.append(idx - 1)

            idx = context_end
            while idx >= context_start and offset[idx][1] >= end_char:
                idx -= 1
            end_positions.append(idx + 1)

    inputs["start_positions"] = start_positions
    inputs["end_positions"] = end_positions
    return inputs

In [44]:
tokenized_squad = jaquad_data.map(preprocess_function, batched=True, remove_columns=jaquad_data["train"].column_names)

  0%|          | 0/32 [00:00<?, ?ba/s]

Loading cached processed dataset at /root/.cache/huggingface/datasets/SkelterLabsInc___ja_qu_ad/default/0.1.0/5847b2e2ab5e02de284395bb15f87f13eae8f6f6ff1f01e4ee9c5c0dcf8ef8eb/cache-235bec00d2678b60.arrow


In [154]:
from transformers import TrainingArguments, Trainer, DefaultDataCollator

data_collator = DefaultDataCollator()

training_args = TrainingArguments(
    output_dir="./results",
    evaluation_strategy="steps",
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=3,
    weight_decay=0.01,
    eval_steps=30
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_squad["train"].select(range(6000)),
    eval_dataset=tokenized_squad["validation"].select(range(200)),
    tokenizer=tokenizer,
    data_collator=data_collator,
)

trainer.train()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
/usr/local/lib/python3.7/dist-packages/transformers/optimization.py:309: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,
***** Running training *****
  Num examples = 6000
  Num Epochs = 3
  Instantaneous batch size per device = 16
  Total train batch size (w. parallel, distributed & accumulation) = 16
  Gradient Accumulation steps = 1
  Total optimization steps = 1125


***** Running Evaluation *****
  Num examples = 200
  Batch size = 16


KeyboardInterrupt: ignored

## Evaluation

In [212]:
import torch
import random

def from_data_to_answer(model, tokenizer, random_data):
  model.eval()
  question, context = random_data['question'], random_data['context']
  input_ids = tokenizer.encode(question, context)
  tokens = tokenizer.convert_ids_to_tokens(input_ids)

  output = model(torch.tensor([input_ids]))
  argmax_start = torch.argmax(output['start_logits'])
  argmax_end = torch.argmax(output['end_logits'])
  print("Question: ", question)
  print("Context:", context)
  print("Predicted answer: ", "".join(tokens[argmax_start:argmax_end]))
  print(argmax_start, argmax_end)
  print("Correct answer: ", "".join(random_data['answers']['text']))

random_data = jaquad_data["validation"][random.randint(0, len(jaquad_data["validation"]))]
from_data_to_answer(model, tokenizer, random_data)

Question:  この文書で紹介している二つの説の共通点は、どんな人々によるギリシャ本土侵入が問題だったと指摘していることなの?
Context: ドーリア人の侵入による説には紀元前13世紀末から始まる『海の民』による移動に伴い、ドーリア人がバルカン半島を南下してギリシャに至ってギリシャ本土南部、ペロポネソス半島、クレタ、小アジア南西部に定住したことによりミケーネ文化が崩壊、ミケーネ人がアテナイ、小アジアの中部へ移住したとしている。また、別の説ではギリシャ本土はドーリア人の侵入によるもので、小アジア西部ではフリュギア人と『海の民』の侵入があったとしている。
Predicted answer:  ドーリア
tensor(26) tensor(28)
Correct answer:  ドーリア人


## Push to Hub

In [82]:
from huggingface_hub import notebook_login

notebook_login()

/usr/local/lib/python3.7/dist-packages/huggingface_hub/hf_api.py:510: FutureWarning: HfApi.login: This method is deprecated in favor of `set_access_token` and will be removed in v0.7.
  FutureWarning,


Login successful
Your token has been saved to /root/.huggingface/token
Authenticated through git-credential store but this isn't the helper defined on your machine.
You might have to re-authenticate when pushing to the Hugging Face Hub. Run the following command in your terminal in case you want to set this credential helper as the default

git config --global credential.helper store


In [145]:
model.save_pretrained("japanese-roberta-question-answering")
tokenizer.save_pretrained("japanese-roberta-question-answering")
model.push_to_hub("japanese-roberta-question-answering", use_temp_dir=True)
tokenizer.push_to_hub("japanese-roberta-question-answering", use_temp_dir=True)

/usr/local/lib/python3.7/dist-packages/huggingface_hub/utils/_deprecation.py:43: FutureWarning: Pass token='japanese-roberta-question-answering' as keyword args. From version 0.7 passing these as positional arguments will result in an error
  FutureWarning,
/usr/local/lib/python3.7/dist-packages/huggingface_hub/hf_api.py:599: FutureWarning: `create_repo` now takes `token` as an optional positional argument. Be sure to adapt your code!
  FutureWarning,
Cloning https://huggingface.co/ybelkada/japanese-roberta-question-answering into local empty directory.


Download file pytorch_model.bin:   0%|          | 16.0k/420M [00:00<?, ?B/s]

Download file spiece.model:   2%|2         | 16.0k/787k [00:00<?, ?B/s]

Clean file spiece.model:   0%|          | 1.00k/787k [00:00<?, ?B/s]

Clean file pytorch_model.bin:   0%|          | 1.00k/420M [00:00<?, ?B/s]

...

Download file pytorch_model.bin:   0%|          | 16.0k/420M [00:00<?, ?B/s]

Download file spiece.model:   2%|1         | 15.6k/787k [00:00<?, ?B/s]

Clean file spiece.model:   0%|          | 1.00k/787k [00:00<?, ?B/s]

Clean file pytorch_model.bin:   0%|          | 1.00k/420M [00:00<?, ?B/s]

tokenizer config file saved in /tmp/tmp79y_t4pf/tokenizer_config.json
Special tokens file saved in /tmp/tmp79y_t4pf/special_tokens_map.json
Copy vocab file to /tmp/tmp79y_t4pf/spiece.model


## Error? To investigate

In [189]:
random_data = jaquad_data["validation"][random.randint(0, len(jaquad_data["validation"]))]
from_data_to_answer(random_data)

Question:  3月12日における国公立大学後期日程の受験者は前年度と比べ、どれだけ減りましたか?
Context: 宮城県教育委員会は、3月14日から18日までを休校とし、15日に予定していた高等学校一般入学試験の合格者発表を22日以降に延期することを決めた。

地震発生直後の2011年3月12日、13日には国公立大学の入学試験後期日程が予定されていたが、12日は被災地にある32校の大学(私立大学含む)で試験が中止されることになった。国立36大学・公立15大学・私立7大学が12日の試験の開始時間繰り下げや、地震の影響を受けた受験生の個別対応を行い、追試の対応をした大学もある。文部科学省は、3月12日における国公立大学後期日程の受験者は6万5667人(昨年から2万604人減少)であり、この減少は地震の影響によるものであるとしている。東北地方で同日に試験が実施された国公立大学は、全12校のうち秋田大学・秋田県立大学のみであった。翌13日においても6校で試験を中止し、5校で繰り下げ実施または個別対応を行った。

また、家屋の損壊した状況に応じて入学金や授業料の免除を行う大学や、震災や計画停電の影響を考慮して授業開始を5月以降とする大学も増えている。
Predicted answer:  6万5667
Correct answer:  2万604人


In [213]:
from transformers import AutoModelForQuestionAnswering,AutoTokenizer,pipeline

context = 'ドーリア人の侵入による説には紀元前13世紀末から始まる『海の民』による移動に伴い、ドーリア人がバルカン半島を南下してギリシャに至ってギリシャ本土南部、ペロポネソス半島、クレタ、小アジア南西部に定住したことによりミケーネ文化が崩壊、ミケーネ人がアテナイ、小アジアの中部へ移住したとしている。また、別の説ではギリシャ本土はドーリア人の侵入によるもので、小アジア西部ではフリュギア人と『海の民』の侵入があったとしている。'
question = "この文書で紹介している二つの説の共通点は、どんな人々によるギリシャ本土侵入が問題だったと指摘していることなの?"
mode_name = 'ybelkada/japanese-roberta-question-answering'
model = AutoModelForQuestionAnswering.from_pretrained(mode_name)
tokenizer = AutoTokenizer.from_pretrained(mode_name)
QA = pipeline('question-answering', model=model, tokenizer=tokenizer)
QA_input = {'question': question,'context':context}
QA(QA_input)

loading configuration file https://huggingface.co/ybelkada/japanese-roberta-question-answering/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/8c665325243570331908cdaac83cde055a8274f79488d012f82cbebdfaf3e49c.2e7e8f53fe123481242b617e35509d18b40bbf52597e6ea8f3ac3dd3f748a98d
Model config RobertaConfig {
  "_name_or_path": "ybelkada/japanese-roberta-question-answering",
  "architectures": [
    "RobertaForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 1,
  "classifier_dropout": null,
  "eos_token_id": 2,
  "gradient_checkpointing": false,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-05,
  "max_position_embeddings": 514,
  "model_type": "roberta",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "pad_token_id": 3,
  "position_embedding_type": "absolute",
  "torch_dtype": "float32",
  "transformers_version": "4

{'answer': 'ドーリア人の侵入による説には紀元前13世紀末から始まる『海の民』による移動に伴い、ドーリア人がバルカン半島を南下してギリシャに至ってギリシャ本土南部、ペロポネソス半島、クレタ、小アジア南西部に定住したことによりミケーネ文化が崩壊、ミケーネ人がアテナイ、小アジアの中部へ移住したとしている。また、別の説ではギリシャ本土はドーリア人の侵入によるもので、小アジア西部ではフリュギア人と『海の民』の侵入があったとしている。',
 'end': 207,
 'score': 0.38383907079696655,
 'start': 0}

In [214]:
from_data_to_answer(model, tokenizer, {"context":context, "question":question, "answers":{"text":['']}})

Question:  この文書で紹介している二つの説の共通点は、どんな人々によるギリシャ本土侵入が問題だったと指摘していることなの?
Context: ドーリア人の侵入による説には紀元前13世紀末から始まる『海の民』による移動に伴い、ドーリア人がバルカン半島を南下してギリシャに至ってギリシャ本土南部、ペロポネソス半島、クレタ、小アジア南西部に定住したことによりミケーネ文化が崩壊、ミケーネ人がアテナイ、小アジアの中部へ移住したとしている。また、別の説ではギリシャ本土はドーリア人の侵入によるもので、小アジア西部ではフリュギア人と『海の民』の侵入があったとしている。
Predicted answer:  ドーリア
tensor(26) tensor(28)
Correct answer:  
